## ⚙️ Environment Setup — Real-Time Activity Recognition

This section sets up the environment for real-time activity recognition using IMU (accelerometer) data.

- It imports the necessary libraries for HTTP requests, data processing, signal analysis, and machine learning.
- It configures the URL to fetch accelerometer readings from a remote device and defines the `window_size` for the rolling data buffer.
- A pre-trained deep learning model (`model_new.keras`) is loaded to classify movements across six possible classes (e.g., push-up rep, sit-up rep, etc.).
- Deques (double-ended queues) are initialized to efficiently store a fixed number of recent sensor readings and detected repetitions.
- A text-to-speech engine (`pyttsx3`) is initialized to provide audible feedback based on the classified movements.

This setup ensures that all necessary components are ready for real-time data streaming, prediction, and feedback.


In [291]:
import requests
import time
import numpy as np
from collections import deque
from tensorflow.keras.models import load_model
from scipy.signal import find_peaks
import pyttsx3
import joblib

# ----------------- Config -----------------
base_url = "http://10.169.26.231:8080"
endpoint = "/get?accX&accY&accZ"
url = base_url + endpoint
window_size = 100

# Load model and scaler
model = load_model('model_new.keras')
#scaler = joblib.load('scaler.pkl')  # Make sure this file exists

# Buffers
sensor_buffer = deque(maxlen=window_size)
rep_buffer_pur = deque(maxlen=window_size)
rep_buffer_sur = deque(maxlen=window_size)
counted_peaks_pur = []
counted_peaks_sur = []
pur_count = 0
sur_count = 0

# TTS
engine = pyttsx3.init()

# Class labels

class_names = {
    0: "Push-Up Rep",   # Push-Up Rep
    1: "Push-Up to Stand",  # Push-Up to Stand
    2: "Stand to Push-Up",  # Stand to Push-Up
    3: "Stand to Sit-Up",  # Stand to Sit-Up
    4: "Sit-Up Rep",   # Sit-Up Rep
    5: "Sit-Up to Stand"   # Sit-Up to Stand
}

## 🌐 `fetch_phyphox_data` Function — Fetching Real-Time Sensor Data

This function, `fetch_phyphox_data()`, retrieves the latest accelerometer readings from a remote server using an HTTP GET request.

- It attempts to extract the `x`, `y`, and `z` acceleration values from the JSON response.
- If any of the acceleration values are missing (`None`), it substitutes small default values (`0.1`) to maintain a continuous data stream.
- Each successful reading is returned as a dictionary containing `x`, `y`, `z`, and a `timestamp`.
- In case of an error (such as a timeout or invalid server response), the function catches the exception, prints a warning message, and returns `None` to indicate that the data fetch failed.

This function ensures reliable and resilient data acquisition, even when occasional transmission errors occur.


In [292]:
def fetch_phyphox_data():
    try:
        response = requests.get(url, timeout=0.5)
        data = response.json()
    
        x = data["buffer"]["accX"]["buffer"][0]
        y = data["buffer"]["accY"]["buffer"][0]
        z = data["buffer"]["accZ"]["buffer"][0]
        
        if x is None or y is None or z is None:
            return {'x': 0.1,
                    'y': 0.1,
                    'z': 0.1,
                    'timestamp': time.time()}
        
        return {'x': x, 'y': y, 'z': z, 'timestamp': time.time()}    
    
    
    
    except Exception as e:
        print(f"⚠ Data fetch error: {str(e)}")
        return None


## 🛠️ `extract_features` Function — Preparing Input Data

The `extract_features(buffer)` function processes a buffer of collected accelerometer data to prepare it for model prediction.

- It separates the x, y, and z axis readings into individual lists.
- It computes the magnitude of each 3D acceleration vector (although the magnitudes are not currently used further).
- The x, y, and z lists are stacked into a NumPy array with shape `(3, window_size)`.
- The array is then transposed to organize the data into shape `(window_size, 3)`, where each row represents a single timestamp of (x, y, z) data.
- Finally, a batch dimension is added to produce an input shape of `(1, window_size, 3)`, making the data ready to be passed into the machine learning model.

This feature extraction step is essential for structuring raw sensor data into a format compatible with the model's expected input.


In [293]:

def extract_features(buffer):
    x = [d['x'] for d in buffer]
    y = [d['y'] for d in buffer]
    z = [d['z'] for d in buffer]
    magnitudes = [np.sqrt(x[i]**2 + y[i]**2 + z[i]**2) for i in range(len(x))]

    features = [
        x,
        y,
        z

    ]
    
    
    features_arr = np.array(features)        # Shape: (3, 100)
    features_correct = features_arr.T           # Shape: (100, 3)
    features_input = features_correct[np.newaxis]
    return features_input

## 🤖 `make_prediction` Function — Running the Model Inference

The `make_prediction(features)` function takes the preprocessed feature input and feeds it directly into the loaded machine learning model to generate a prediction.

- It expects the input features to be properly shaped for the model.
- It calls the model's `predict` method and returns the output, which typically contains the class probabilities.

This function serves as the bridge between data preprocessing and obtaining real-time activity predictions.


In [294]:

def make_prediction(features):

    return model.predict(features)


## 📈 `count_reps` Function — Peak Detection for Repetitions

The `count_reps(buffer, counted_peaks, min_prominence=0.3, min_distance=20)` function identifies new peaks in a time-series signal, which correspond to detected repetitions (reps).

- It takes in a buffer of magnitude values (a list or array of movement strengths).
- It uses the `find_peaks` method from `scipy.signal` to detect peaks based on:
  - **Minimum Prominence**: Ensures only significant peaks are detected (default: `0.3`).
  - **Minimum Distance**: Ensures detected peaks are spaced apart enough (default: `20` samples).
- After detecting peaks, it filters out any peaks that have already been counted by comparing them to the `counted_peaks` list.
- The function returns a list of **new peak indices**, representing **newly detected reps** during the session.

This method is crucial for reliably tracking repetitions like push-ups and sit-ups from real-time sensor data.


In [295]:

def count_reps(buffer, counted_peaks, min_prominence=0.3, min_distance=20):
    magnitudes = np.array(buffer)
    peaks, _ = find_peaks(magnitudes, prominence=min_prominence, distance=min_distance)
    new_peaks = [p for p in peaks if p not in counted_peaks]
    return new_peaks

## 🔵 Real-Time Prediction and Monitoring Loop

This section runs the main real-time data streaming and activity classification loop.

- It continuously fetches accelerometer data from the server and calculates the total magnitude of the acceleration vector.
- New data points are appended to a rolling sensor buffer.
- Once the buffer is full and the total magnitude exceeds a threshold (≥ 1.5), the data is processed into features and passed into the pre-trained model for prediction.
- The model predicts the current movement class, and both the predicted label and class probabilities are printed for live monitoring.
- Commented-out sections allow for counting push-up and sit-up repetitions by detecting peaks in the movement magnitude signals.
- Text-to-speech feedback (optional) is set up to announce the detected repetitions out loud.
- The loop runs indefinitely until a keyboard interrupt (`Ctrl+C`) occurs, after which a session summary is printed and read out using speech synthesis.

This loop enables live activity recognition and rep counting using real-time IMU sensor data.

In [ ]:
from math import sqrt
print("📡 Starting stream with PUR/SUR counting...")


try:
    while True:
        new_data = fetch_phyphox_data()
        
        total=0
        
        if new_data is None:
            time.sleep(0.1)
            new_data = fetch_phyphox_data()
            continue
        else:
            total=sqrt(new_data['x']**2+new_data['y']**2+new_data['z']**2)

        sensor_buffer.append(new_data)
       
        print(f"the total is : {total}")
        if len(sensor_buffer) >= window_size and total>=1.5:
            print(total)
            features = extract_features(sensor_buffer)
            prediction = make_prediction(features)
            predicted_class = np.argmax(prediction)
            label = class_names.get(predicted_class, "Other")
            
            
            
            #if total>=0.2:
            if label != 'Push-Up to Stand':
                print(prediction)
                print(f"\n🧠 Predicted: {label}")
                print(f"🔢 Probabilities: {[f'{p:.3f}' for p in prediction[0]]}")  # Note [0] to get first row

        # Get current magnitude signal
            #magnitudes = [np.sqrt(d['x']**2 + d['y']**2 + d['z']**2) for d in sensor_buffer]

            # If pur (class 0)
            #if predicted_class == 0:
                #rep_buffer_pur.extend(magnitudes)
                #if len(rep_buffer_pur) == rep_buffer_pur.maxlen:
                    #peaks = count_reps(rep_buffer_pur, counted_peaks_pur)
                    #for _ in peaks:
                        #pur_count += 1
                        #print(f"🔁 PUR Rep {pur_count}")
                        #engine.say(f"Push up rep {pur_count}")
                        #engine.runAndWait()
                    #counted_peaks_pur.extend(peaks)

            # If sur (class 4)
            #elif predicted_class == 4:
                #rep_buffer_sur.extend(magnitudes)
                #if len(rep_buffer_sur) == rep_buffer_sur.maxlen:
                    #peaks = count_reps(rep_buffer_sur, counted_peaks_sur)
                    #for _ in peaks:
                        #sur_count += 1
                        #print(f"🔁 SUR Rep {sur_count}")
                        #engine.say(f"Sit up rep {sur_count}")
                       # engine.runAndWait()
                   # counted_peaks_sur.extend(peaks)


        time.sleep(0.05)

except KeyboardInterrupt:
    print("\n🛑 Session ended.")
    print(f"\n📋 Session Summary:")
    print(f"  🔹 Push-Up Reps (pur): {pur_count}")
    print(f"  🔸 Sit-Up Reps (sur): {sur_count}")
    engine.say("Workout session complete.")
    engine.say(f"You did {pur_count} push-ups and {sur_count} sit-ups.")
    engine.runAndWait()


📡 Starting stream with PUR/SUR counting...
the total is : 0.07718267861988946
the total is : 0.07617654739996857
the total is : 0.07713481962136137
the total is : 0.09344165501651555
the total is : 0.09099165342496542
the total is : 0.07672985005294793
the total is : 0.07647723155820105
the total is : 0.06941942857486616
the total is : 0.07117156058123772
the total is : 0.08184992157435159
the total is : 0.06851775038146561
the total is : 0.06957540561983704
the total is : 0.07996351276669268
the total is : 0.08408728926114253
the total is : 0.07008576001125956
the total is : 0.07904397324931885
the total is : 0.08176811658089696
the total is : 0.08153877007522724
the total is : 0.07694998723265299
the total is : 0.09655499586576105
the total is : 0.10355143552047133
the total is : 0.07672985005294793
the total is : 0.09211364246144427
the total is : 0.0336555401616574
the total is : 0.11300977288611895
the total is : 0.07004680372458026
the total is : 0.09167834078521969
the total is 

⚠ Data fetch error: HTTPConnectionPool(host='10.169.26.231', port=8080): Max retries exceeded with url: /get?accX&accY&accZ (Caused by ConnectTimeoutError(<urllib3.connection.HTTPConnection object at 0x0000012E2A57E520>, 'Connection to 10.169.26.231 timed out. (connect timeout=0.5)'))
⚠ Data fetch error: HTTPConnectionPool(host='10.169.26.231', port=8080): Max retries exceeded with url: /get?accX&accY&accZ (Caused by ConnectTimeoutError(<urllib3.connection.HTTPConnection object at 0x0000012E2A57E8E0>, 'Connection to 10.169.26.231 timed out. (connect timeout=0.5)'))
⚠ Data fetch error: HTTPConnectionPool(host='10.169.26.231', port=8080): Max retries exceeded with url: /get?accX&accY&accZ (Caused by ConnectTimeoutError(<urllib3.connection.HTTPConnection object at 0x0000012DB62CD610>, 'Connection to 10.169.26.231 timed out. (connect timeout=0.5)'))
⚠ Data fetch error: HTTPConnectionPool(host='10.169.26.231', port=8080): Max retries exceeded with url: /get?accX&accY&accZ (Caused by Connect

1/1 [==============================] - 0s 28ms/step
[[9.9485874e-01 4.5522327e-05 5.0957897e-03]]

🧠 Predicted: Nothing
🔢 Probabilities: ['0.995', '0.000', '0.005']
the total is : 2.45828437031004
2.45828437031004
1/1 [==============================] - 0s 29ms/step
[[9.937186e-01 4.776743e-05 6.233661e-03]]

🧠 Predicted: Nothing
🔢 Probabilities: ['0.994', '0.000', '0.006']
the total is : 2.45828437031004
2.45828437031004
1/1 [==============================] - 0s 32ms/step
[[9.9309134e-01 4.5484769e-05 6.8632155e-03]]

🧠 Predicted: Nothing
🔢 Probabilities: ['0.993', '0.000', '0.007']
the total is : 2.45828437031004
2.45828437031004
1/1 [==============================] - 0s 29ms/step
[[9.9271810e-01 4.3491360e-05 7.2383983e-03]]

🧠 Predicted: Nothing
🔢 Probabilities: ['0.993', '0.000', '0.007']
the total is : 2.45828437031004
2.45828437031004
1/1 [==============================] - 0s 29ms/step
[[9.9245304e-01 4.1716437e-05 7.5052404e-03]]

🧠 Predicted: Nothing
🔢 Probabilities: ['0.992', 

the total is : 0.5658669220790578
the total is : 0.6540216714895732
the total is : 1.6780878630726568
1.6780878630726568
1/1 [==============================] - 0s 40ms/step
[[2.0104971e-02 4.6427645e-05 9.7984856e-01]]

🧠 Predicted: Sit up reps
🔢 Probabilities: ['0.020', '0.000', '0.980']
the total is : 1.0540856470714348
the total is : 0.6887251666728156
the total is : 2.5709098801251042
2.5709098801251042
1/1 [==============================] - 0s 29ms/step
[[2.1709213e-02 4.8146172e-05 9.7824270e-01]]

🧠 Predicted: Sit up reps
🔢 Probabilities: ['0.022', '0.000', '0.978']
the total is : 1.811810772072277
1.811810772072277
1/1 [==============================] - 0s 35ms/step
[[2.2545110e-02 5.0041253e-05 9.7740483e-01]]

🧠 Predicted: Sit up reps
🔢 Probabilities: ['0.023', '0.000', '0.977']
the total is : 2.690294680788441
2.690294680788441
1/1 [==============================] - 0s 35ms/step
[[2.2745559e-02 4.8182985e-05 9.7720623e-01]]

🧠 Predicted: Sit up reps
🔢 Probabilities: ['0.023'

the total is : 0.828277008616409
the total is : 0.8323518123088677
the total is : 4.402925280878402
4.402925280878402
1/1 [==============================] - 0s 30ms/step
[[9.9454099e-01 6.1402679e-05 5.3975857e-03]]

🧠 Predicted: Nothing
🔢 Probabilities: ['0.995', '0.000', '0.005']
the total is : 0.2670691805246877
the total is : 0.25968752428183756
the total is : 0.29882457082977765
the total is : 1.5030927933614573
1.5030927933614573
1/1 [==============================] - 0s 39ms/step
[[9.9601513e-01 6.5382766e-05 3.9193896e-03]]

🧠 Predicted: Nothing
🔢 Probabilities: ['0.996', '0.000', '0.004']
the total is : 1.3405165468117117
the total is : 1.6642727749454145
1.6642727749454145
1/1 [==============================] - 0s 51ms/step
[[9.9726403e-01 5.1085575e-05 2.6848433e-03]]

🧠 Predicted: Nothing
🔢 Probabilities: ['0.997', '0.000', '0.003']
the total is : 0.8127301846433928
the total is : 0.6374343788923267
the total is : 3.156364118504329
3.156364118504329
1/1 [===================

...

the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.173

the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.173

the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.173

the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.173

the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.17320508075688776
the total is : 0.173